# Analyse et Nettoyage du dataset UE

Seuls les véhicules des années 2022-2023 et de la France ont été exportés à partir de https://www.eea.europa.eu/data-and-maps/data/co2-cars-emission-20

# <font color='#3585CD'>Importation des librairies</font>

In [10]:
import warnings
warnings.filterwarnings('ignore')
warnings.warn('DelftStack')
warnings.warn('Do not show this message')

import pandas as pd

import numpy as np

import matplotlib.pyplot as plt

import seaborn as sns

import plotly.figure_factory as ff
import plotly.express as px
import plotly.graph_objects as go

import kagglehub

from scipy.stats import gaussian_kde

import sys
import os

# <font color='#3585CD'>Fonctions qui seront utilisées dans ce notebook</font>

In [11]:
def analyser_variable_categorielle_plotly(df, variable, top_n=100, display_array=True):
  """
  Analyse une variable catégorielle en affichant un DataFrame des 'top_n' catégories les plus fréquentes, ainsi qu'un graphique.

  :param df: DataFrame contenant la variable à analyser.
  :param variable: Nom de la variable catégorielle.
  :param top_n: Nombre de catégories à afficher (par défaut 100).
  """

  if display_array == True:
    top_cat = f"(Top {top_n} catégories)" if top_n != 100 else ""
    print(f"\n Analyse de la variable : {variable} {top_cat}")

  # Calcul des fréquences et pourcentages
  category_counts = df[variable].value_counts().head(top_n)
  category_percent = df[variable].value_counts(normalize=True).head(top_n) * 100

  # Création d’un DataFrame avec Libellé, Total et Pourcentage
  df_summary = pd.DataFrame({
      "Libellé": category_counts.index,
      "Total": category_counts.values,
      "Pourcentage": category_percent.values
  })

  # Affichage du tableau de synthèse
  display(df_summary)

  # Création du graphique interactif avec Plotly
  nb = top_n
  if top_n == 100:
    nb = ""
  fig = px.bar(df_summary,
                x="Libellé",
                y="Total",
                text="Total",
                title=f'Distribution des {nb} premières catégories de {variable}',
                labels={"Libellé": variable, "Total": "Nombre d'occurrences"},
                template="plotly_white")

  fig.update_traces(textposition='outside')
  fig.update_layout(xaxis_tickangle=-45)

  # Affichage du graphique
  fig.show()

def analyser_variables_numeriques_plotly(df, variables, bins=30):
    """
    Analyse les variables numériques en affichant un histogramme + KDE (distribution) et un boxplot interactifs.

    :param df: DataFrame contenant les données.
    :param variables: Liste des variables numériques à analyser.
    :param bins: Nombre de bins pour l'histogramme (par défaut 30).
    """
    for var in variables:
        #print(f"\n Analyse de la variable : {var}")
        #display(df[var].describe())  # Affichage des statistiques descriptives

        # Supprimer les valeurs NaN
        data = df[var].dropna()

        # Histogramme
        hist = go.Histogram(
            x=data,
            nbinsx=bins,
            marker=dict(color='skyblue', line=dict(color='black', width=1)),  # Bordures noires
            opacity=0.6,  # Semi-transparent pour voir la KDE
            name="Histogramme"
        )

        # Calcul des densités pour la courbe KDE
        kde = gaussian_kde(data)
        x_vals = np.linspace(data.min(), data.max(), 500)  # Intervalle lissé
        kde_vals = kde(x_vals)

        # Courbe KDE
        kde_curve = go.Scatter(
            x=x_vals,
            y=kde_vals * len(data) * (data.max() - data.min()) / bins,  # Mise à l'échelle par rapport à l'histogramme
            mode='lines',
            line=dict(color='blue', width=2),
            name="Densité (KDE)"
        )

        # Création de la figure combinée
        fig = go.Figure(data=[hist, kde_curve])

        # Mise en page
        fig.update_layout(
            title=f'Distribution de {var} (Histogramme + KDE)',
            xaxis_title="Valeur",
            yaxis_title="Fréquence",
            template="plotly_white",
            barmode='overlay'
        )

        # Affichage du graphique combiné
        fig.show()

        # Création du boxplot
        boxplot = go.Box(
            x=data,
            marker=dict(color='salmon'),
            name="Boxplot",
            boxpoints="outliers"  # Affichage des outliers
        )

        # Création et affichage du Boxplot
        fig_box = go.Figure(data=[boxplot])
        fig_box.update_layout(
            title=f'Boxplot de {var}',
            xaxis_title="Valeur",
            template="plotly_white"
        )

        fig_box.show()


def display_missing_values(df):
  """
  Affiche un DataFrame contenant les valeurs manquantes, leur pourcentage / nombre et leur type, pour chaque colonne du DataFrame.

  :param df: DataFrame contenant la variable à analyser.
  """
  missing_values = df.isnull().sum()
  missing_ratio = (missing_values / len(df)) * 100

  missing_values_df = pd.DataFrame({
      'Colonne': missing_values.index,
      'Valeurs manquantes (%)': missing_ratio.values,
      'Nombre de valeurs manquantes': missing_values.values,
      'Type': df.dtypes.values
  })

  missing_values_df = missing_values_df[missing_values_df['Nombre de valeurs manquantes'] > 0]
  missing_values_df = missing_values_df.sort_values(by='Valeurs manquantes (%)', ascending=False).reset_index(drop=True)

  return missing_values_df

def afficher_boxplot(df, colonne, couleur="blue"):
  """
  Affiche un boxplot interactif pour une variable donnée.

  :param df: DataFrame contenant les données.
  :param colonne: Nom de la colonne à analyser.
  :param couleur: Couleur du boxplot (par défaut 'blue').
  """

  # Création de la figure
  fig = go.Figure()

  # Ajout du boxplot
  fig.add_trace(go.Box(
      x=df[colonne].dropna(),
      name=colonne,
      marker_color=couleur
  ))

  # Mise en page
  fig.update_layout(
      title=f"Box Plot des valeurs de {colonne}",
      xaxis_title=colonne,
      showlegend=False
  )

  # Affichage du graphique
  fig.show()

def plot_correlation_matrix(df):
  """
  Affiche la matrice de corrélation des variables numériques sous forme de heatmap interactive avec Plotly.

  :param df: DataFrame Pandas contenant les données
  """
  # Sélection des colonnes numériques
  num_numeric_cols = df.select_dtypes(include=['number']).columns

  # Calcul de la matrice de corrélation
  corr_matrix = df[num_numeric_cols].corr()

  # Création de la heatmap avec Plotly (labels en bas et à gauche)
  fig = ff.create_annotated_heatmap(
      z=corr_matrix.values,
      x=list(corr_matrix.columns),
      y=list(corr_matrix.index),
      colorscale="RdBu_r",
      annotation_text=corr_matrix.round(2).values,
      showscale=True
  )

  # Ajustement de la disposition
  fig.update_layout(
      title="Matrice de corrélation des variables numériques",
      height=600, width=800,
      xaxis=dict(side="bottom", tickangle=-45),
      yaxis=dict(side="left")
  )

  # Affichage
  fig.show()

def calculer_correlation(df, col1, col2):
  """
  Calcule et affiche la corrélation entre deux colonnes d'un DataFrame.

  Paramètres :
  df :DataFrame contenant les données.
  col1 : nom de la première colonne.
  col2 : nom de la deuxième colonne.

  Retourne la valeur de la corrélation et une interprétation de son intensité.
  """
  correlation = df[col1].corr(df[col2])
  print(f"Corrélation entre {col1} et {col2} : {correlation:.2f}")

  if abs(correlation) > 0.8:
      interpretation = "Très forte corrélation"
  elif abs(correlation) > 0.6:
      interpretation = "Forte corrélation"
  elif abs(correlation) > 0.4:
      interpretation = "Corrélation modérée"
  elif abs(correlation) > 0.15:
      interpretation = "Corrélation faible"
  else:
      interpretation = "Pas de corrélation linéaire significative"

  print(interpretation + ".\n")

  return correlation, interpretation

def detecter_outliers_plotly(df, seuil=1.5):
  """
  Détecte les outliers pour chaque variable numérique d'un DataFrame en utilisant la méthode IQR.
  Affiche également un Boxplot interactif pour chaque variable.

  :param df: DataFrame contenant les données.
  :param seuil: Seuil du coefficient IQR (par défaut 1.5).
  :return: DataFrame contenant le nombre d'outliers et le pourcentage par variable.
  """
  outliers_dict = {}

  for col in df.select_dtypes(include=['number']).columns:  # Sélectionner les colonnes numériques
      Q1 = df[col].quantile(0.25)  # Premier quartile
      Q3 = df[col].quantile(0.75)  # Troisième quartile
      IQR = Q3 - Q1  # Calcul de l'intervalle interquartile

      # Détection des valeurs aberrantes
      lower_bound = Q1 - seuil * IQR
      upper_bound = Q3 + seuil * IQR
      outliers = df[(df[col] < lower_bound) | (df[col] > upper_bound)]

      # Stocker les résultats
      nb_outliers = outliers.shape[0]
      perc_outliers = (nb_outliers / df.shape[0]) * 100
      outliers_dict[col] = {"Nb_Outliers": nb_outliers, "Pourcentage": round(perc_outliers, 2)}

      # Création du Boxplot avec Plotly
      fig = go.Figure()
      fig.add_trace(go.Box(
          x=df[col],
          name=col,
          marker_color='blue',
          boxpoints='outliers'
      ))

      # Mise en page
      fig.update_layout(
          title=f"Box Plot de {col}",
          xaxis_title="Valeur",
          yaxis_title="Variable",
          template="plotly_white",
          showlegend=False
      )

      fig.show()

  # Conversion en DataFrame
  df_outliers = pd.DataFrame.from_dict(outliers_dict, orient='index')

  return df_outliers

def analyse_columns(df):

    """
    Analyse les colonnes d'un DataFrame : nom, type, nombre de valeurs uniques et exemples de valeurs.

    :param df: DataFrame Pandas
    :return: DataFrame avec l'analyse des colonnes
    """
    analysis = []

    for col in df.columns:
        col_name = col
        col_type = df[col].dtype
        unique_count = df[col].nunique()  # Nombre de valeurs uniques
        unique_values = df[col].dropna().unique()[:5].tolist()  # Exemples (max 5)
        unique_values = " | ".join(map(str, unique_values))  # Séparateur : " | "

        analysis.append({
            'Nom de la colonne': col_name,
            'Type de la colonne': col_type,
            'Nombre de valeurs uniques': unique_count,
            'Exemples de valeurs': unique_values
        })

    return pd.DataFrame(analysis)

def plot_scatter_co2(df, x, y="CO2", color="Carburant", size="CO2"):
  """
  Génère un scatter plot interactif avec Plotly, avec une ligne de moyenne CO2.

  Paramètres :
  - df : DataFrame contenant les données
  - x : Nom de la colonne pour l'axe X
  - y : Nom de la colonne pour l'axe Y (par défaut "CO2")
  - color : Nom de la colonne pour la couleur des points (par défaut "Carburant")
  - size : Nom de la colonne pour la taille des points (par défaut "CO2")
  """

  # Calcul de la moyenne globale du CO2
  moyenne_co2 = df[y].mean()

  # Création du scatter plot
  fig = px.scatter(
      df,
      x=x,
      y=y,
      color=color,
      size=size,
      title=f"Relation entre {x} et {y}",
      labels={x: x.capitalize(), y: y.capitalize(), color: color.capitalize()},
      hover_data=df.columns,
      size_max=20
  )

  # Ajout de la ligne de moyenne CO2
  fig.add_hline(
      y=moyenne_co2,
      line_dash="dot",
      line_color="red",
      annotation_text=f"Moyenne CO2: {moyenne_co2:.2f} g/km",
      annotation_position="top right",
      annotation_font_color="red",
      annotation_font_size=12,
      annotation_bgcolor="rgba(255,255,255,0.7)"
  )

  fig.show()


def analyser_hist_co2_par_variable(df, variable, top_n=50, order='desc', co2="CO2"):
  """
  Génère un histogramme interactif avec Plotly, avec une ligne de moyenne CO2.

  Paramètres :
  :param df : DataFrame contenant les données
  :param variable : Nom de la colonne à analyser
  :param top_n: Nombre de catégories à afficher (par défaut 50).
  :param order: Ordonnancement des catégories (par défaut 'desc').
  :param co2: Nom de la colonne des émissions de CO2 (par défaut "CO2")
  """
  ascending = True if order == 'asc' else False

  df_co2 = df.groupby(variable)[co2].mean().sort_values(ascending=ascending).reset_index()
  df_co2 = df_co2.head(top_n)

  df_co2['CO2_txt'] = df_co2[co2].apply(lambda x: f"{x:.2f}")

  moyenne_co2 = df[co2].mean()

  fig = px.bar(
      df_co2,
      x=variable,
      y=co2,
      title=f"Distribution des émissions de CO2 par {variable} (Top {top_n})",
      labels={variable: variable.capitalize(), co2: "Émissions de CO2 (g/km)"},
      color=co2,
      color_continuous_scale="RdYlGn_r",
      text='CO2_txt'
  )

  # Ligne de moyenne du CO2
  fig.add_hline(
      y=moyenne_co2,
      line_dash="dot",
      line_color="red",
      annotation_text=f"Moyenne CO2: {moyenne_co2:.2f} g/km",
      annotation_position="top right",
      annotation_font_color="red",
      annotation_font_size=12,
      annotation_bgcolor="rgba(255,255,255,0.7)"
  )

  fig.update_layout(
      xaxis_tickangle=-75,
      coloraxis_colorbar=dict(title="CO2 (g/km)"),
      uniformtext_minsize=8,
      uniformtext_mode='hide'
  )

  fig.show()

def detecter_outliers_plotly_var(serie, seuil=1.5):
    """
    Détecte les outliers pour une seule variable numérique en utilisant la méthode IQR.
    Affiche également un Boxplot interactif.

    :param serie: Série Pandas contenant les valeurs de la variable.
    :param seuil: Seuil du coefficient IQR (par défaut 1.5).
    :return: DataFrame contenant le nombre d'outliers et le pourcentage.
    """
    if not isinstance(serie, pd.Series):
        raise ValueError("Veuillez fournir une variable sous forme de pd.Series")

    Q1 = serie.quantile(0.25)  # Premier quartile
    Q3 = serie.quantile(0.75)  # Troisième quartile
    IQR = Q3 - Q1  # Intervalle interquartile

    # Détection des valeurs aberrantes
    lower_bound = Q1 - seuil * IQR
    upper_bound = Q3 + seuil * IQR
    outliers = serie[(serie < lower_bound) | (serie > upper_bound)]

    # Résultats
    nb_outliers = outliers.shape[0]
    perc_outliers = (nb_outliers / serie.shape[0]) * 100

    # Création du Boxplot avec Plotly
    fig = go.Figure()
    fig.add_trace(go.Box(
        x=serie,
        name=serie.name if serie.name else "Variable",
        marker_color='blue',
        boxpoints='outliers'
    ))

    # Mise en page
    fig.update_layout(
        title=f"Box Plot de {serie.name if serie.name else 'Variable'}",
        xaxis_title="Valeur",
        yaxis_title="Variable",
        template="plotly_white",
        showlegend=False
    )

    fig.show()

    # Résultats sous forme de DataFrame
    df_outliers = pd.DataFrame({
        "Nb_Outliers": [nb_outliers],
        "Pourcentage": [round(perc_outliers, 2)]
    }, index=[serie.name if serie.name else "Variable"])

    return df_outliers


# <font color='#3585CD'>Chargement des données</font>

## Chargement du dataset principal

In [12]:
# Le dataset étant volumineux pour être dans le repository Github, nous le téléchargeons via Kaggle test
path = kagglehub.dataset_download("dimitrileloup/vehicules-fr-2022-2023")
print("Chemin vers le fichier : ", path)

Chemin vers le fichier :  /root/.cache/kagglehub/datasets/dimitrileloup/vehicules-fr-2022-2023/versions/1


In [13]:
dataset_path = f"{path}/datas_FR_2022_2023.csv"
df = pd.read_csv(dataset_path)
df.head(10)

ID Country                  VFN          Mp        Mh         Man  \
0  76627138      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   
1  76627139      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   
2  76627140      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   
3  76627141      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   
4  76627142      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   
5  76627143      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   
6  76627144      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   
7  76627145      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   
8  76627146      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   
9  76627147      FR  IP-03_BU_0214-1C4-1  STELLANTIS  CHRYSLER  FCA US LLC   

   MMS                 Tan   T     Va  ... Erwltp (g/km)  De  Vf Status  year  \
0  NaN  e3*2007/46*0300*33  BU  AXT23  ...           NaN NaN NaN      F  2022   
1  NaN  e3*2007/46*0300*32  BU  AXT23  ...           NaN NaN NaN      F  2022   
2  NaN  e3*2007/46*0300*33  BU  AXT23  ...           NaN NaN NaN      F  2022   
3  NaN  e3*2007/46*0300*33  BU  AXT23  ...           NaN NaN NaN      F  2022   
4  NaN  e3*2007/46*0300*33  BU  AXT23  ...           NaN NaN NaN      F  2022   
5  NaN  e3*2007/46*0300*33  BU  AXT23  ...           NaN NaN NaN      F  2022   
6  NaN  e3*2007/46*0300*32  BU  AXT23  ...           NaN NaN NaN      F  2022   
7  NaN  e3*2007/46*0300*33  BU  AXT23  ...           NaN NaN NaN      F  2022   
8  NaN  e3*2007/46*0300*33  BU  AXT23  ...           NaN NaN NaN      F  2022   
9  NaN  e3*2007/46*0300*32  BU  AXT23  ...           NaN NaN NaN      F  2022   

   Date of registration  Fuel consumption   ech  RLFI  Electric range (km)  
0            2022-01-25                2.0  NaN   NaN                 43.0  
1            2022-02-16                2.0  NaN   NaN                 43.0  
2            2022-02-24                2.0  NaN   NaN                 43.0  
3            2022-02-28                2.0  NaN   NaN                 43.0  
4            2022-01-28                2.0  NaN   NaN                 43.0  
5            2022-04-21                2.0  NaN   NaN                 43.0  
6            2022-01-28                2.0  NaN   NaN                 43.0  
7            2022-04-21                2.0  NaN   NaN                 43.0  
8            2022-04-22                2.0  NaN   NaN                 43.0  
9            2022-01-31                2.0  NaN   NaN                 43.0  

[10 rows x 40 columns]

In [14]:
# Suppression des espaces accidentels dans les noms des colonnes comme "Fuel consumption "
df.columns = df.columns.str.strip()

## Chargement du dataset du dictionnaire des variables

In [15]:
path_vars = kagglehub.dataset_download("dimitrileloup/dfinition-des-colonnes")
print("Path to dataset files:", path_vars)

Path to dataset files: /root/.cache/kagglehub/datasets/dimitrileloup/dfinition-des-colonnes/versions/1


In [16]:
pd.set_option('display.max_colwidth', None) # pour pouvoir afficher tout le descriptif
dataset_variables = f"{path_vars}/Table-definition.xlsx"
var = pd.read_excel(dataset_variables)
var.head(40)

Nom de la variable  \
0                     ID   
1                Country   
2                    VFN   
3                     Mp   
4                     Mh   
5                    Man   
6                    MMS   
7                    Tan   
8                      T   
9                     Va   
10                    Ve   
11                    Mk   
12                    Cn   
13                    Ct   
14                    Cr   
15                     r   
16                m (kg)   
17                    Mt   
18          Enedc (g/km)   
19          Ewltp (g/km)   
20                W (mm)   
21              At1 (mm)   
22              At2 (mm)   
23                    Ft   
24                    Fm   
25              ec (cm3)   
26               ep (KW)   
27             z (Wh/km)   
28                    IT   
29         Ernedc (g/km)   
30         Erwltp (g/km)   
31                    De   
32                    Vf   
33                Status   
34                  year   
35  Date of registration   
36      Fuel consumption   
37                   ech   
38                  RLFI   
39   Electric range (km)   

                                                             Descriptif  \
0                                                           Identifiant   
1                                                                  Pays   
2                    Numéro d'identification de la famille du véhicule.   
3                                                Pool des constructeurs   
4                       Nom du fabricant Dénomination standard de l'UE.   
5                                  Déclaration OEM du nom du fabricant.   
6                         Nom du fabricant Dénomination du registre MS.   
7                                        Numéro d'homologation de type.   
8                                                                  Type   
9                                                              Variante   
10                                                              Version   
11                                                               Marque   
12                                                       Nom commercial   
13                           Catégorie du type de véhicule réceptionné.   
14                                   Catégorie du véhicule immatriculé.   
15                                    Total des nouvelles inscriptions.   
16                  Masse en ordre de marche Véhicule terminé/complet .   
17                                                  Masse d’essai WLTP.   
18                                 Émissions spécifiques de CO2 (NEDC).   
19                                 Émissions spécifiques de CO2 (WLTP).   
20                                                          Empattement   
21                                   Largeur d'essieu essieu directeur.   
22                                       Largeur d'essieu autre essieu.   
23                                                   Type de carburant.   
24                                                      Mode carburant.   
25                                                  Capacité du moteur.   
26                                                 Puissance du moteur.   
27                                   Consommation d'énergie électrique.   
28          Technologie innovante ou groupe de technologies innovantes.   
29         Réduction des émissions grâce à des technologies innovantes.   
30  Réduction des émissions grâce à des technologies innovantes (WLTP).   
31                                                Facteur de déviation.   
32                                             Facteur de vérification.   
33                        P = Données provisoires, F = Données finales.   
34                                                Année de déclaration.   
35                                                Date d'enregistrement   
36                                           Consommation de carburant.   
37     

# <font color='#3585CD'>Premières analyses</font>

## Informations sur le dataset

In [17]:
print("\nAperçu du dataset :")
print(df.info())


Aperçu du dataset :
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3528480 entries, 0 to 3528479
Data columns (total 40 columns):
 #   Column                Dtype  
---  ------                -----  
 0   ID                    int64  
 1   Country               object 
 2   VFN                   object 
 3   Mp                    object 
 4   Mh                    object 
 5   Man                   object 
 6   MMS                   float64
 7   Tan                   object 
 8   T                     object 
 9   Va                    object 
 10  Ve                    object 
 11  Mk                    object 
 12  Cn                    object 
 13  Ct                    object 
 14  Cr                    object 
 15  r                     int64  
 16  m (kg)                float64
 17  Mt                    float64
 18  Enedc (g/km)          float64
 19  Ewltp (g/km)          int64  
 20  W (mm)                float64
 21  At1 (mm)              float64
 22  At2 (mm)             

## Satistiques descriptives

In [18]:
print("\nStatistiques descriptives :")
display(df.describe(include='number').T)


Statistiques descriptives :


count          mean           std     min  \
ID                   3528480.0  1.013037e+08  2.222407e+07  2281.0   
MMS                        0.0           NaN           NaN     NaN   
r                    3528480.0  1.000000e+00  0.000000e+00     1.0   
m (kg)               3528479.0  1.433451e+03  3.009387e+02   570.0   
Mt                   3528479.0  1.547239e+03  3.138880e+02   616.0   
Enedc (g/km)          284171.0  9.175725e+00  1.574223e+01     0.0   
Ewltp (g/km)         3528480.0  9.972159e+01  5.134716e+01     0.0   
W (mm)               1638878.0  2.634966e+03  1.318641e+02  1873.0   
At1 (mm)             1638878.0  1.543811e+03  5.045288e+01  1220.0   
At2 (mm)             1637695.0  1.541500e+03  5.550988e+01  1301.0   
ec (cm3)             3008185.0  1.399706e+03  3.837714e+02   658.0   
ep (KW)              3515652.0  9.708175e+01  4.785103e+01    28.0   
z (Wh/km)             813305.0  1.660274e+02  2.816681e+01    99.0   
Ernedc (g/km)              0.0           NaN           NaN     NaN   
Erwltp (g/km)        2518566.0  1.560700e+00  4.959278e-01     0.5   
De                         0.0           NaN           NaN     NaN   
Vf                         0.0           NaN           NaN     NaN   
year                 3528480.0  2.022536e+03  4.987362e-01  2022.0   
Fuel consumption     3008200.0  5.115726e+00  1.479071e+00     0.4   
Electric range (km)   813305.0  2.668318e+02  1.768213e+02    12.0   

                             25%           50%           75%           max  
ID                   77509525.75  1.211759e+08  1.220580e+08  1.229402e+08  
MMS                          NaN           NaN           NaN           NaN  
r                           1.00  1.000000e+00  1.000000e+00  1.000000e+00  
m (kg)                   1197.00  1.367000e+03  1.603000e+03  2.965000e+03  
Mt                       1303.00  1.481000e+03  1.732000e+03  3.150000e+03  
Enedc (g/km)                0.00  0.000000e+00  2.700000e+01  4.900000e+01  
Ewltp (g/km)               96.00  1.200000e+02  1.320000e+02  5.720000e+02  
W (mm)                   2552.00  2.605000e+03  2.680000e+03  3.665000e+03  
At1 (mm)                 1513.00  1.550000e+03  1.575000e+03  1.776000e+03  
At2 (mm)                 1506.00  1.542000e+03  1.580000e+03  1.758000e+03  
ec (cm3)                 1197.00  1.332000e+03  1.580000e+03  7.993000e+03  
ep (KW)                    69.00  8.800000e+01  1.100000e+02  1.177000e+03  
z (Wh/km)                 151.00  1.590000e+02  1.720000e+02  4.400000e+02  
Ernedc (g/km)                NaN           NaN           NaN           NaN  
Erwltp (g/km)               1.14  1.750000e+00  1.970000e+00  2.780000e+00  
De                           NaN           NaN           NaN           NaN  
Vf                           NaN           NaN           NaN           NaN  
year                     2022.00  2.023000e+03  2.023000e+03  2.023000e+03  
Fuel consumption            4.80  5.300000e+00  5.900000e+00  2.520000e+01  
Electric range (km)        66.00  2.920000e+02  4.330000e+02  7.350000e+02

In [19]:
df.describe(include="object").T

count unique                       top     freq
Country               3528480      1                        FR  3528480
VFN                   3528474   3084  IP-JAA1MTPJT4A_000-VF1-1    78050
Mp                    3326798     14                STELLANTIS  1050427
Mh                    3528480     81                   RENAULT   637662
Man                   3528480     80               RENAULT SAS   637719
Tan                   3528479   3636        e2*2007/46*0639*20    55694
T                     3528479    448                         U   391555
Va                    3528479   2156                         P   190019
Ve                    3528478   9620                    V/AMXS    37623
Mk                    3528480     80                   RENAULT   564592
Cn                    3528480   1266                        C3   144250
Ct                    3528480      2                        M1  3469781
Cr                    3528480      2                        M1  3469781
Ft                    3528480      9                    petrol  2005953
Fm                    3528480      6                         M  1784863
IT                    2518566     97                  e2 28 29   395137
Status                3528480      1                         F  3528480
Date of registration  3528480    715                2023-09-29    22320
ech                   1791945     19                 Euro 6 AP   932731
RLFI                    62932     85                      N.A.    22867

## Nombre de valeurs uniques par colonne

In [20]:
# Calculer le nombre de valeurs uniques par colonne et renommer la colonne
df_unique_values = df.nunique().sort_values(ascending=False).reset_index()
df_unique_values.columns = ["colonne", "nombre de valeurs uniques"]

df_unique_values

colonne  nombre de valeurs uniques
0                     ID                    3528480
1                     Ve                       9620
2                    Tan                       3636
3                    VFN                       3084
4                     Va                       2156
5                     Mt                       2070
6                 m (kg)                       1276
7                     Cn                       1266
8   Date of registration                        715
9    Electric range (km)                        587
10                     T                        448
11          Ewltp (g/km)                        350
12                W (mm)                        270
13               ep (KW)                        252
14              At2 (mm)                        240
15              At1 (mm)                        230
16             z (Wh/km)                        222
17         Erwltp (g/km)                        180
18      Fuel consumption                        164
19              ec (cm3)                        106
20                    IT                         97
21                  RLFI                         85
22                    Mh                         81
23                   Man                         80
24                    Mk                         80
25          Enedc (g/km)                         25
26                   ech                         19
27                    Mp                         14
28                    Ft                          9
29                    Fm                          6
30                    Ct                          2
31                    Cr                          2
32                  year                          2
33               Country                          1
34                Status                          1
35                     r                          1
36                   MMS                          0
37         Ernedc (g/km)                          0
38                    De                          0
39                    Vf                          0

## Analyse rapide des colonnes
<p>La fonction analyse_columns permet de visualiser les différentes colonnes avec un échantillon de valeurs</p>

In [21]:
analysis_df = analyse_columns(df)
analysis_df

Nom de la colonne Type de la colonne  Nombre de valeurs uniques  \
0                     ID              int64                    3528480   
1                Country             object                          1   
2                    VFN             object                       3084   
3                     Mp             object                         14   
4                     Mh             object                         81   
5                    Man             object                         80   
6                    MMS            float64                          0   
7                    Tan             object                       3636   
8                      T             object                        448   
9                     Va             object                       2156   
10                    Ve             object                       9620   
11                    Mk             object                         80   
12                    Cn             object                       1266   
13                    Ct             object                          2   
14                    Cr             object                          2   
15                     r              int64                          1   
16                m (kg)            float64                       1276   
17                    Mt            float64                       2070   
18          Enedc (g/km)            float64                         25   
19          Ewltp (g/km)              int64                        350   
20                W (mm)            float64                        270   
21              At1 (mm)            float64                        230   
22              At2 (mm)            float64                        240   
23                    Ft             object                          9   
24                    Fm             object                          6   
25              ec (cm3)            float64                        106   
26               ep (KW)            float64                        252   
27             z (Wh/km)            float64                        222   
28                    IT             object                         97   
29         Ernedc (g/km)            float64                          0   
30         Erwltp (g/km)            float64                        180   
31                    De            float64                          0   
32                    Vf            float64                          0   
33                Status             object                          1   
34                  year              int64                          2   
35  Date of registration             object                        715   
36      Fuel consumption            float64                        164   
37                   ech             object                         19   
38                  RLFI             object                         85   
39   Electric range (km)            float64                        587   

                                                                                                 Exemples de valeurs  
0                                                               76627138 | 76627139 | 76627140 | 76627141 | 76627142  
1                                                                                                                 FR  
2   IP-03_BU_0214-1C4-1 | IP-E4JLESSSPOSAH-1C4-1 | IP-E4JLESSRUB-1C4-1 | IP-E4JLPHEVSAH-1C4-1 | IP-e4JLPHEVSAH-1C4-1  
3                       STELLANTIS | TESLA-HONDA-JLR | FORD | MAZDA-SUBARU-SUZUKI-TOYOTA | RENAULT-NISSAN-MITSUBISHI  
4                                   CHRYSLER | HONDA MOTOR CO | FORD MOTOR COMPANY | GENERAL MOTORS HOLDINGS | MAZDA  
5       FCA US LLC | HONDA MOTOR CO LTD | FORD MOTOR COMPANY | GENERAL MOTORS HOLDINGS LLC | MAZDA MOTOR CORPORATION  
6                                                                                                                     
7          e3*2007/4

# <font color='#3585CD'>Analyse des valeurs manquantes</font>

In [22]:
data_na = display_missing_values(df)
data_na

Colonne  Valeurs manquantes (%)  Nombre de valeurs manquantes  \
0                   MMS              100.000000                       3528480   
1                    Vf              100.000000                       3528480   
2         Ernedc (g/km)              100.000000                       3528480   
3                    De              100.000000                       3528480   
4                  RLFI               98.216456                       3465548   
5          Enedc (g/km)               91.946362                       3244309   
6             z (Wh/km)               76.950273                       2715175   
7   Electric range (km)               76.950273                       2715175   
8              At2 (mm)               53.586388                       1890785   
9                W (mm)               53.552861                       1889602   
10             At1 (mm)               53.552861                       1889602   
11                  ech               49.214818                       1736535   
12                   IT               28.621786                       1009914   
13        Erwltp (g/km)               28.621786                       1009914   
14             ec (cm3)               14.745585                        520295   
15     Fuel consumption               14.745159                        520280   
16                   Mp                5.715832                        201682   
17              ep (KW)                0.363556                         12828   
18                  VFN                0.000170                             6   
19                   Ve                0.000057                             2   
20                   Mt                0.000028                             1   
21                  Tan                0.000028                             1   
22               m (kg)                0.000028                             1   
23                   Va                0.000028                             1   
24                    T                0.000028                             1   

       Type  
0   float64  
1   float64  
2   float64  
3   float64  
4    object  
5   float64  
6   float64  
7   float64  
8   float64  
9   float64  
10  float64  
11   object  
12   object  
13  float64  
14  float64  
15  float64  
16   object  
17  float64  
18   object  
19   object  
20  float64  
21   object  
22  float64  
23   object  
24   object

# <font color='#3585CD'>Suppression de colonnes</font>

Nous pouvons dès à présent ces colonnes qui ont un taux de valeurs manquantes supérieur à 70% :

*   At2 (mm)
*   W (mm)
*   MMS
*   Vf
*   De
*   Ernedc (g/km)
*   At1 (mm)
*   Enedc (g/km)
*   RLFI
*   z (Wh/km)
*   Electric range (km)

In [26]:
df = df.drop(columns=['At2 (mm)', 'W (mm)', 'MMS', 'Vf', 'De', 'Ernedc (g/km)',	'At1 (mm)',	'Enedc (g/km)',	'RLFI',	'z (Wh/km)', 'Electric range (km)'], axis=1)

KeyError: "['At2 (mm)', 'W (mm)', 'MMS', 'Vf', 'De', 'Ernedc (g/km)', 'At1 (mm)', 'Enedc (g/km)', 'RLFI', 'z (Wh/km)', 'Electric range (km)'] not found in axis"

In [24]:
df.duplicated().sum()

np.int64(0)

In [27]:
data_na = display_missing_values(df)
data_na

Colonne  Valeurs manquantes (%)  Nombre de valeurs manquantes  \
0                ech               49.214818                       1736535   
1                 IT               28.621786                       1009914   
2      Erwltp (g/km)               28.621786                       1009914   
3           ec (cm3)               14.745585                        520295   
4   Fuel consumption               14.745159                        520280   
5                 Mp                5.715832                        201682   
6            ep (KW)                0.363556                         12828   
7                VFN                0.000170                             6   
8                 Ve                0.000057                             2   
9                Tan                0.000028                             1   
10                Va                0.000028                             1   
11                 T                0.000028                             1   
12            m (kg)                0.000028                             1   
13                Mt                0.000028                             1   

       Type  
0    object  
1    object  
2   float64  
3   float64  
4   float64  
5    object  
6   float64  
7    object  
8    object  
9    object  
10   object  
11   object  
12  float64  
13  float64

# <font color='#3585CD'>Suppresion des colonnes non pertinentes</font>

Certaines colonnes n'ont pas d'intérêt à être gardées :

*   IT
*   Erwltp (g/km) (dépreciée)
*   ID : identifiant du véhicule
*   Country : notre dataset est une extraction des véhicules de France
*   VFN : n'a pas de norme universelle et comporte trop de valeurs
*   Tan : trop de valeurs et sans intérêt pour notre projet
*   T : trop de valeurs et sans intérêt pour notre projet
*   Va : trop de valeurs et sans intérêt pour notre projet
*   Ve : trop de valeurs et sans intérêt pour notre projet
*   Status : n'a qu'une seule valeur et ne varie pas
*   Year : 1 seule valeur
*   Date of registration : sans intérêt pour notre projet
*   Fm : redondant avec Ft
*   Cr : nous avons 2 catégories (M1, M1G). M1G est une sous-catégorie de M1 réservée aux véhicules tout-terrain. Nous pouvons conclure que tous les véhicules sont de catégorie M1
*   Ct : idem que Cr
*   ech : sans intérêt pour notre projet
*   Mp : redondant, se retrouve dans une autre colonne
*   Man : redondant avec Mk
*   r : n'a qu'une seule valeur
*   Mh : redondant avec Mk


In [28]:
df = df.drop(columns=['IT', 'Erwltp (g/km)', 'ID', 'Country', 'VFN', 'Tan', 'T', 'Va', 'Ve', 'Status', 'year', 'Date of registration', 'Fm', 'Cr', 'Ct', 'ech', 'Mp', 'Man', 'r', 'Mh'], axis=1)

## Vérification de la corrélation entre Masse à vide et Masse totale</font>

In [29]:
df_masse = df[['Mt', 'm (kg)']]
plot_correlation_matrix(df_masse)

On se rend compte qu'il y a une **forte corrélataion** entre ces 2 variables, qui pourrait entrainer une **colinéarité**. Nous prenons la décision de ne garder que la masse à vide (m (kg))

In [30]:
df = df.drop('Mt', axis=1)

# <font color='#3585CD'>Gestion des doublons</font>

## Nombre de doublons

In [31]:
df.duplicated().sum()

np.int64(3503825)

## Supression des doublons

In [32]:
df.drop_duplicates(inplace =True)

In [33]:
df.duplicated().sum()

np.int64(0)

In [34]:
df.shape

(24655, 8)

In [35]:
df = df.reset_index(drop=True)

# <font color='#3585CD'>Renommage des colonnes</font>

Pour plus de compréhension, nous allons renommer les colonnes :



*   Mk : Marque
*   Cn : Modele
*   Ewltp (g/km) : Co2
*   Ft : Carburant
*   ec (cm3) : Cylindree moteur
*   ep (KW) : Puissance moteur
*   Fuel consumption : Consommation carburant


In [36]:
renommage = {
    'Mk': 'Marque',
    'Cn': 'Modèle',
    'm (kg)' : 'Masse à vide',
    'Ewltp (g/km)': 'CO2',
    'Ft': 'Carburant',
    'ec (cm3)': 'Cylindrée moteur',
    'ep (KW)': 'Puissance moteur',
    'Fuel consumption': 'Consommation carburant'
}

# Application du renommage
df.rename(columns=renommage, inplace=True)

In [37]:
df

Marque              Modèle  Masse à vide  CO2        Carburant  \
0               JEEP            RENEGADE        1845.0   49  petrol/electric   
1               JEEP            WRANGLER        1883.0  244           petrol   
2               JEEP            WRANGLER        1972.0  259           petrol   
3               JEEP            WRANGLER        1972.0  258           petrol   
4               JEEP  WRANGLER UNLIMITED        2348.0   79  petrol/electric   
...              ...                 ...           ...  ...              ...   
24650          SKODA               SCALA        1211.0  119           petrol   
24651           FORD      TRANSIT CUSTOM        2311.0  197           diesel   
24652  MERCEDES-BENZ               A 200        1440.0  144           petrol   
24653  MERCEDES-BENZ            V-KLASSE        2220.0  225           diesel   
24654           FORD      TRANSIT CUSTOM        2167.0  205           diesel   

       Cylindrée moteur  Puissance moteur  Consommation carburant  
0                1332.0              96.0                     2.0  
1                1995.0             200.0                    10.8  
2                1995.0             200.0                    11.5  
3                1995.0             200.0                    11.5  
4                1995.0             200.0                     3.5  
...                 ...               ...                     ...  
24650             999.0              70.0                     5.2  
24651            1995.0              95.0                     7.5  
24652            1332.0             120.0                     6.3  
24653            1950.0             174.0                     8.6  
24654            1995.0              95.0                     7.8  

[24655 rows x 8 columns]

# <font color='#3585CD'>Faut-il garder les véhicules électriques et hydrogènes ?</font>
Notre objectif est de prédire les émissions directes de CO2. Garder les véhicules électriques et hydrogènes risque de biaiser notre modèle. Nous allons donc exclure les véhicules électriques de notre dataset

In [38]:
# Vérification des émissions de CO2 des véhicules hydrogènes
df_hydrogen = df[df["Carburant"] == "hydrogen"]
df_hydrogen['CO2'].value_counts()

CO2
0    4
Name: count, dtype: int64

In [39]:
# Nous excluons les véhicules électriques et hydrogènes
df = df[(df["Carburant"] != "electric") & (df["Carburant"] != "hydrogen")]

In [40]:
df.shape

(23935, 8)

# <font color='#3585CD'>Traitement des valeurs manquantes</font>

In [41]:
data_na = display_missing_values(df)
data_na

Colonne  Valeurs manquantes (%)  \
0            Masse à vide                0.004178   
1  Consommation carburant                0.004178   

   Nombre de valeurs manquantes     Type  
0                             1  float64  
1                             1  float64

## Gestion des valeurs manquantes de la colonne Consommation carburant

In [42]:
df_fc_na = df[df['Consommation carburant'].isna()]
df_fc_na

Marque              Modèle  Masse à vide  CO2 Carburant  \
23942  LAND ROVER  RANGE ROVER EVOQUE           NaN  137    diesel   

       Cylindrée moteur  Puissance moteur  Consommation carburant  
23942            1998.0             120.0                     NaN

Nous allons gérer cette ligne

In [43]:
# regardons si d'autres modeles RANGE ROVER EVOQUE sont renseignés
df_jag_evoque = df[(df['Modèle'] == 'RANGE ROVER EVOQUE') & (df['Carburant'] == 'diesel') & (~df['Consommation carburant'].isna())]
df_jag_evoque.head()

Marque              Modèle  Masse à vide  CO2 Carburant  \
2931  LAND ROVER  RANGE ROVER EVOQUE        1967.0  170    diesel   
2932  LAND ROVER  RANGE ROVER EVOQUE        1992.0  172    diesel   
2933  LAND ROVER  RANGE ROVER EVOQUE        1992.0  175    diesel   
2934  LAND ROVER  RANGE ROVER EVOQUE        1992.0  173    diesel   
2935  LAND ROVER  RANGE ROVER EVOQUE        1992.0  174    diesel   

      Cylindrée moteur  Puissance moteur  Consommation carburant  
2931            1998.0             120.0                     6.5  
2932            1998.0             150.0                     6.6  
2933            1998.0             150.0                     6.7  
2934            1998.0             150.0                     6.6  
2935            1998.0             150.0                     6.6

In [44]:
fc_mean_jag_evoque = df_jag_evoque['Consommation carburant'].mean().round(1)
fc_mean_jag_evoque

np.float64(6.5)

In [45]:
df.loc[(df["Modèle"] == "RANGE ROVER EVOQUE") & (df['Consommation carburant'].isna()), "Consommation carburant"] = fc_mean_jag_evoque

In [46]:
data_na = display_missing_values(df)
data_na

Colonne  Valeurs manquantes (%)  Nombre de valeurs manquantes     Type
0  Masse à vide                0.004178                             1  float64

## Gestion des valeurs manquantes de la colonne Masse à vide

In [47]:
data_na = display_missing_values(df)
data_na

Colonne  Valeurs manquantes (%)  Nombre de valeurs manquantes     Type
0  Masse à vide                0.004178                             1  float64

In [48]:
df_mkg_na = df[df['Masse à vide'].isna()]
df_mkg_na

Marque              Modèle  Masse à vide  CO2 Carburant  \
23942  LAND ROVER  RANGE ROVER EVOQUE           NaN  137    diesel   

       Cylindrée moteur  Puissance moteur  Consommation carburant  
23942            1998.0             120.0                     6.5

Recherchons dans le dataset si nous avons des modèles équivalents dont les variables m (kg) et Mt ne sont **pas nulles**

In [49]:
df_jag_lr = df[(df['Modèle'] == 'RANGE ROVER EVOQUE') & (df['Carburant'] == 'diesel') & (df['Puissance moteur'] == 120) & (~df['Masse à vide'].isna())]
df_jag_lr

Marque              Modèle  Masse à vide  CO2 Carburant  \
2931  LAND ROVER  RANGE ROVER EVOQUE        1967.0  170    diesel   
2936  LAND ROVER  RANGE ROVER EVOQUE        1967.0  173    diesel   
2937  LAND ROVER  RANGE ROVER EVOQUE        1967.0  171    diesel   
2940  LAND ROVER  RANGE ROVER EVOQUE        1967.0  174    diesel   
2941  LAND ROVER  RANGE ROVER EVOQUE        1967.0  172    diesel   
2943  LAND ROVER  RANGE ROVER EVOQUE        1967.0  172    diesel   
2969  LAND ROVER  RANGE ROVER EVOQUE        1855.0  164    diesel   
2970  LAND ROVER  RANGE ROVER EVOQUE        1855.0  160    diesel   
2971  LAND ROVER  RANGE ROVER EVOQUE        1855.0  165    diesel   
2972  LAND ROVER  RANGE ROVER EVOQUE        1855.0  162    diesel   

      Cylindrée moteur  Puissance moteur  Consommation carburant  
2931            1998.0             120.0                     6.5  
2936            1998.0             120.0                     6.6  
2937            1998.0             120.0                     6.5  
2940            1998.0             120.0                     6.6  
2941            1998.0             120.0                     6.6  
2943            1998.0             120.0                     6.5  
2969            1998.0             120.0                     6.3  
2970            1998.0             120.0                     6.1  
2971            1998.0             120.0                     6.3  
2972            1998.0             120.0                     6.2

In [50]:
fc_mean_masse_jag_evoque = df_jag_evoque['Masse à vide'].mean().round(1)
fc_mean_masse_jag_evoque

np.float64(1955.3)

In [51]:
# pour les mêmes modèles, la variable Masse à vide est égale à 1967
df['Masse à vide'] = df['Masse à vide'].fillna(fc_mean_masse_jag_evoque)

In [52]:
# Vérification
df.loc[23942].to_frame().T

Marque              Modèle Masse à vide  CO2 Carburant  \
23942  LAND ROVER  RANGE ROVER EVOQUE       1955.3  137    diesel   

      Cylindrée moteur Puissance moteur Consommation carburant  
23942           1998.0            120.0                    6.5

In [53]:
data_na = display_missing_values(df)
data_na

Empty DataFrame
Columns: [Colonne, Valeurs manquantes (%), Nombre de valeurs manquantes, Type]
Index: []

In [54]:
# ré inisialisation des indexes
df = df.reset_index(drop=True)
df

Marque              Modèle  Masse à vide  CO2        Carburant  \
0               JEEP            RENEGADE        1845.0   49  petrol/electric   
1               JEEP            WRANGLER        1883.0  244           petrol   
2               JEEP            WRANGLER        1972.0  259           petrol   
3               JEEP            WRANGLER        1972.0  258           petrol   
4               JEEP  WRANGLER UNLIMITED        2348.0   79  petrol/electric   
...              ...                 ...           ...  ...              ...   
23930          SKODA               SCALA        1211.0  119           petrol   
23931           FORD      TRANSIT CUSTOM        2311.0  197           diesel   
23932  MERCEDES-BENZ               A 200        1440.0  144           petrol   
23933  MERCEDES-BENZ            V-KLASSE        2220.0  225           diesel   
23934           FORD      TRANSIT CUSTOM        2167.0  205           diesel   

       Cylindrée moteur  Puissance moteur  Consommation carburant  
0                1332.0              96.0                     2.0  
1                1995.0             200.0                    10.8  
2                1995.0             200.0                    11.5  
3                1995.0             200.0                    11.5  
4                1995.0             200.0                     3.5  
...                 ...               ...                     ...  
23930             999.0              70.0                     5.2  
23931            1995.0              95.0                     7.5  
23932            1332.0             120.0                     6.3  
23933            1950.0             174.0                     8.6  
23934            1995.0              95.0                     7.8  

[23935 rows x 8 columns]

# <font color='#3585CD'>Distribution des variables catégorielles</font>

## Analyse par marque

### Valeurs uniques

In [55]:
sorted(df['Marque'].unique())

['ALFA ROMEO',
 'ALPINA',
 'ALPINE',
 'ASTON MARTIN',
 'AUDI',
 'BENTLEY',
 'BMW',
 'BUGATTI',
 'CADILLAC',
 'CASELANI',
 'CATERHAM',
 'CHEVROLET',
 'CITROEN',
 'CUPRA',
 'DACIA',
 'DALLARA',
 'DONKERVOORT',
 'DR',
 'DS',
 'FERRARI',
 'FIAT',
 'FORD',
 'FORD-CNG-TECHNIK',
 'HONDA',
 'HYUNDAI',
 'INEOS',
 'JAGUAR',
 'JEEP',
 'KIA',
 'KTM',
 'LAMBORGHINI',
 'LAND ROVER',
 'LEXUS',
 'LOTUS',
 'LYNK&CO',
 'MASERATI',
 'MAZDA',
 'MC LAREN',
 'MCLAREN',
 'MERCEDES AMG',
 'MERCEDES BENZ',
 'MERCEDES-BENZ',
 'MG',
 'MINI',
 'MITSUBISHI',
 'MITSUBISHI MOTORS (THAILAND)',
 'MITSUBISHI MOTORS CORPORATION',
 'MITSUBISHI MOTORS THAILAND',
 'MORGAN',
 'NISSAN',
 'OPEL',
 'PEUGEOT',
 'PORSCHE',
 'RENAULT',
 'ROLLS ROYCE',
 'ROLLS-ROYCE',
 'SEAT',
 'SECMA',
 'SKODA',
 'SSANGYONG',
 'SUBARU',
 'SUZUKI',
 'TOYOTA',
 'VOLKSWAGEN',
 'VOLVO']

### Remplacement

Certaines valeurs peuvent être regroupées, comme par exemple :

*   'MC LAREN', 'MCLAREN'
*   'MERCEDES AMG', 'MERCEDES BENZ', 'MERCEDES-BENZ'
*   'MITSUBISHI', 'MITSUBISHI MOTORS CORPORATION', 'MITSUBISHI MOTORS THAILAND'


In [56]:
replace_mk = {'MC LAREN' : 'MCLAREN',
              'MERCEDES AMG' : 'MERCEDES BENZ',
              'MERCEDES-BENZ' : 'MERCEDES BENZ',
              'MITSUBISHI MOTORS CORPORATION' : 'MITSUBISHI',
              'MITSUBISHI MOTORS THAILAND' : 'MITSUBISHI',
              'MITSUBISHI MOTORS (THAILAND)' : 'MITSUBISHI',
              'FORD-CNG-TECHNIK' : 'FORD',
              'ROLLS ROYCE' : 'ROLLS-ROYCE'}
df['Marque'] = df['Marque'].replace(replace_mk)

In [57]:
df['Marque'].nunique()

57

### Analyse

In [58]:
analyser_variable_categorielle_plotly(df, 'Marque', 58)


 Analyse de la variable : Marque (Top 58 catégories)


Libellé  Total  Pourcentage
0             BMW   3645    15.228745
1   MERCEDES BENZ   2853    11.919783
2           SKODA   2413    10.081471
3            AUDI   2043     8.535617
4      VOLKSWAGEN   2011     8.401922
5            FORD   1474     6.158346
6         RENAULT   1199     5.009400
7         PEUGEOT    992     4.144558
8            SEAT    956     3.994151
9            MINI    603     2.519323
10     LAND ROVER    540     2.256110
11         TOYOTA    488     2.038855
12        CITROEN    457     1.909338
13           OPEL    456     1.905160
14        HYUNDAI    456     1.905160
15            KIA    331     1.382912
16           FIAT    301     1.257573
17        PORSCHE    283     1.182369
18          VOLVO    279     1.165657
19             DS    254     1.061207
20          CUPRA    249     1.040318
21         NISSAN    227     0.948402
22          MAZDA    205     0.856486
23          DACIA    204     0.852308
24         JAGUAR    178     0.743681
25     ALFA ROMEO    177     0.739503
26           JEEP    155     0.647587
27         SUZUKI     88     0.367662
28       MASERATI     74     0.309171
29          HONDA     51     0.213077
30          LEXUS     49     0.204721
31        BENTLEY     30     0.125339
32     MITSUBISHI     25     0.104450
33         ALPINE     25     0.104450
34   ASTON MARTIN     22     0.091916
35        FERRARI     20     0.083560
36    LAMBORGHINI     18     0.075204
37         SUBARU     14     0.058492
38       CATERHAM     11     0.045958
39         ALPINA     10     0.041780
40    ROLLS-ROYCE     10     0.041780
41             MG      8     0.033424
42         MORGAN      7     0.029246
43        MCLAREN      6     0.025068
44          LOTUS      5     0.020890
45      SSANGYONG      5     0.020890
46          SECMA      4     0.016712
47      CHEVROLET      4     0.016712
48       CADILLAC      3     0.012534
49             DR      3     0.012534
50        LYNK&CO      3     0.012534
51        BUGATTI      3     0.012534
52          INEOS      3     0.012534
53    DONKERVOORT      2     0.008356
54        DALLARA      1     0.004178
55       CASELANI      1     0.004178
56            KTM      1     0.004178

## Analyse par carburant

### Valeurs uniques

In [59]:
sorted(df['Carburant'].unique())

['diesel', 'diesel/electric', 'e85', 'lpg', 'ng', 'petrol', 'petrol/electric']

### Remplacement

Certaines valeurs peuvent être regroupées :



*   'diesel/electric' & 'petrol/electric' sont des véhicules hybride
*   'lpg' & 'ng' sont des énergies au gaz
*   'petrol' sera renommé en 'essence' pour plus de compréhension.


In [60]:
replace_ft = {
              'petrol' : 'essence',
              'diesel/electric' : 'hybride',
              'petrol/electric' : 'hybride',
              'lpg' : 'gaz',
              'ng' : 'gaz'}
df['Carburant'] = df['Carburant'].replace(replace_ft)

### Analyse

In [61]:
analyser_variable_categorielle_plotly(df, 'Carburant')


 Analyse de la variable : Carburant 


Libellé  Total  Pourcentage
0  essence  11445    47.817004
1   diesel   9554    39.916440
2  hybride   2370     9.901817
3      e85    449     1.875914
4      gaz    117     0.488824

## Analyse par modèle de voiture

In [62]:
analyser_variable_categorielle_plotly(df, 'Modèle', 30)


 Analyse de la variable : Modèle (Top 30 catégories)


Libellé  Total  Pourcentage
0           OCTAVIA    546     2.281178
1            KODIAQ    464     1.938584
2             FOCUS    451     1.884270
3              GOLF    420     1.754752
4            SUPERB    384     1.604345
5            TIGUAN    384     1.604345
6             KAROQ    300     1.253395
7          DEFENDER    262     1.094631
8        SEAT ATECA    254     1.061207
9            TRAFIC    252     1.052851
10             PUMA    238     0.994360
11            T-ROC    236     0.986004
12      VITO TOURER    195     0.814706
13            FABIA    191     0.797995
14       OCTAVIA RS    188     0.785461
15            KAMIQ    179     0.747859
16   TRANSIT CUSTOM    171     0.714435
17         V-KLASSE    168     0.701901
18           FIESTA    158     0.660121
19        SEAT LEON    157     0.655943
20             POLO    157     0.655943
21              508    154     0.643409
22           KANGOO    149     0.622519
23            ARONA    147     0.614163
24         A4 AVANT    147     0.614163
25              308    144     0.601629
26           PASSAT    139     0.580740
27  TOURNEO CONNECT    138     0.576562
28            IBIZA    138     0.576562
29           ARTEON    133     0.555672

# <font color='#3585CD'>Distribution des variables numériques</font>

## Sélection des colonnes numériques

In [63]:
# Sélection des colonnes numériques
num_vars = df.select_dtypes(include=['int64', 'float64']).columns.tolist()
num_vars

['Masse à vide',
 'CO2',
 'Cylindrée moteur',
 'Puissance moteur',
 'Consommation carburant']

## Analyse de la masse du véhicule Masse à vide

In [64]:
analyser_variables_numeriques_plotly(df, ['Masse à vide'])

## Analyse des émissions spécifiques de CO2

In [65]:
analyser_variables_numeriques_plotly(df, ['CO2'], 30)

## Analyse de la cylindrée moteur

In [67]:
analyser_variables_numeriques_plotly(df, ['Cylindrée moteur'], 50)

## Analyse de la puissance du moteur

In [66]:
analyser_variables_numeriques_plotly(df, ['Puissance moteur'])

## Analyse de la Consommation carburant

In [68]:
analyser_variables_numeriques_plotly(df, ['Consommation carburant'])

# <font color='#3585CD'>Création d'indicateurs</font>

## Indicateur de Charge Spécifique du Moteur (ICSM)

`ICSM = Puissance (kW) / Masse du véhicule (kg)`

**Interprétation** :

*   Faible ICSM → Voiture puissante et légère (moins d’effort, moins de CO₂).
*   Élevé ICSM → Voiture sous-motorisée (forte sollicitation, plus de CO₂).

In [69]:
df['ICSM'] = df['Puissance moteur'] / df['Masse à vide']

## Indicateur de Consommation Énergétique (ICE)

`ICE = Puissance (kW) / Cylindrée (cm³)`

**Interprétation** :

*   Faible ICE → Moteur optimisé (ex. turbo downsizing).
*   Élevé ICE → Moteur gourmand et peu efficient.

In [70]:
df['ICE'] = df['Puissance moteur'] / df['Cylindrée moteur']

## Indicateur de Densité Energétique du Carburant (IDEC)

`IDEC = Cylindrée (cm³) / Masse du véhicule (kg)`

**Interprétation** :

*   Faible IDEC → Moteur bien dimensionné (moins d’effort, moins de CO₂).
*   Élevé IDEC → Moteur sous-dimensionné (forte sollicitation, plus de CO₂).

In [71]:
df['IDEC'] = df['Cylindrée moteur'] / df['Masse à vide']

# <font color='#3585CD'>Analyse du CO2 en fonction de certaines variables</font>

### Analyse du CO2 en fonction de la masse du véhicule

In [72]:
plot_scatter_co2(df, "Masse à vide")

Output hidden; open in https://colab.research.google.com to view.

On observe que les véhicules plus lourds tendent à émettre plus de CO₂, avec une distinction entre les types de carburant.

### Analyse du CO2 en fonction de la puissance du moteur.

In [73]:
plot_scatter_co2(df, "Puissance moteur")

Output hidden; open in https://colab.research.google.com to view.

### Analyse du CO2 en fonction du carburant



In [74]:
plot_scatter_co2(df, "Carburant")

Output hidden; open in https://colab.research.google.com to view.

In [75]:
analyser_hist_co2_par_variable(df, 'Carburant')

### Analyse du CO2 en fonction de la marque

**Top des marques les plus polluantes**

In [76]:
analyser_hist_co2_par_variable(df, 'Marque', 36)

### Analyse du CO2 en fonction du modèle de voiture

**Top des modèles les plus polluants**

In [77]:
analyser_hist_co2_par_variable(df, 'Modèle', 30)

**Top des modèles les moins polluants**

In [78]:
analyser_hist_co2_par_variable(df, 'Modèle', 30, order='asc')

### Analyse du CO2 en fonction de la consommation

In [79]:
plot_scatter_co2(df, "Consommation carburant")

Output hidden; open in https://colab.research.google.com to view.

### Analyse du CO2 en fonction des indicateurs ICSM, ICE, IDEC

In [80]:
plot_scatter_co2(df, "ICSM")

Output hidden; open in https://colab.research.google.com to view.

In [81]:
plot_scatter_co2(df, "ICE")

Output hidden; open in https://colab.research.google.com to view.

In [82]:
plot_scatter_co2(df, "IDEC")

Output hidden; open in https://colab.research.google.com to view.

# <font color='#3585CD'>Corrélation des variables numériques</font>

In [83]:
plot_correlation_matrix(df)

In [84]:
num_numeric_cols = df.select_dtypes(include=['number']).columns
num_numeric_cols

for col in num_numeric_cols:
  calculer_correlation(df, col, 'CO2')

Corrélation entre Masse à vide et CO2 : 0.17
Corrélation faible.

Corrélation entre CO2 et CO2 : 1.00
Très forte corrélation.

Corrélation entre Cylindrée moteur et CO2 : 0.45
Corrélation modérée.

Corrélation entre Puissance moteur et CO2 : 0.44
Corrélation modérée.

Corrélation entre Consommation carburant et CO2 : 0.97
Très forte corrélation.

Corrélation entre ICSM et CO2 : 0.46
Corrélation modérée.

Corrélation entre ICE et CO2 : 0.13
Pas de corrélation linéaire significative.

Corrélation entre IDEC et CO2 : 0.45
Corrélation modérée.



# <font color='#3585CD'>Analyse des outliers</font>

## Masse à vide

In [85]:
detecter_outliers_plotly_var(df['Masse à vide'])

Nb_Outliers  Pourcentage
Masse à vide          800         3.34

In [86]:
df_outliers_masse = df[df['Masse à vide'] < 750].sort_values(by='Masse à vide', ascending=True)
df_outliers_masse.head(20)

Marque             Modèle  Masse à vide  CO2 Carburant  \
2976   CATERHAM           SEVEN S3         570.0  109   essence   
5150      SECMA           FUN 1600         658.0  142   essence   
5151      SECMA     FUN 1600 BUGGY         668.0  142   essence   
2977   CATERHAM           SEVEN S3         700.0  191   essence   
2980   CATERHAM           SEVEN S3         700.0  145   essence   
2981   CATERHAM           SEVEN SV         700.0  191   essence   
2978   CATERHAM           SEVEN S3         700.0  145   essence   
2979   CATERHAM           SEVEN S3         700.0  145   essence   
15692  CATERHAM           SEVEN S3         700.0  148   essence   
2983   CATERHAM           SEVEN SV         700.0  145   essence   
2982   CATERHAM           SEVEN SV         725.0  191   essence   
2984   CATERHAM          SEVEN CSR         725.0  191   essence   
16478  CATERHAM           SEVEN SV         725.0  148   essence   
5152      SECMA     FUN 1600 TURBO         748.0  132   essence   
5153      SECMA  FUN 1600 TURBO GT         748.0  132   essence   

       Cylindrée moteur  Puissance moteur  Consommation carburant      ICSM  \
2976              658.0              62.0                     4.8  0.108772   
5150             1598.0              77.0                     6.3  0.117021   
5151             1598.0              77.0                     6.3  0.115269   
2977             1999.0             176.0                     6.4  0.251429   
2980             1596.0             100.0                     8.3  0.142857   
2981             1999.0             176.0                     6.4  0.251429   
2978             1596.0             100.0                     6.4  0.142857   
2979             1596.0             100.0                     8.5  0.142857   
15692            1999.0             127.0                     6.7  0.181429   
2983             1596.0             100.0                     8.5  0.142857   
2982             1999.0             176.0                     6.4  0.242759   
2984             1999.0             176.0                     6.4  0.242759   
16478            1999.0             127.0                     6.5  0.175172   
5152             1598.0             165.0                     5.8  0.220588   
5153             1598.0             165.0                     5.8  0.220588   

            ICE      IDEC  
2976   0.094225  1.154386  
5150   0.048185  2.428571  
5151   0.048185  2.392216  
2977   0.088044  2.855714  
2980   0.062657  2.280000  
2981   0.088044  2.855714  
2978   0.062657  2.280000  
2979   0.062657  2.280000  
15692  0.063532  2.855714  
2983   0.062657  2.280000  
2982   0.088044  2.757241  
2984   0.088044  2.757241  
16478  0.063532  2.757241  
5152   0.103254  2.136364  
5153   0.103254  2.136364

In [87]:
df_outliers_masse = df[df['Masse à vide'] > 2500].sort_values(by='Masse à vide', ascending=True)
df_outliers_masse.tail(20)

Marque             Modèle  Masse à vide  CO2 Carburant  \
23315            BMW           XM LABEL        2795.0   42   hybride   
15627            BMW           XM LABEL        2795.0   44   hybride   
22757            BMW           XM LABEL        2795.0   39   hybride   
17115            BMW           XM LABEL        2795.0   41   hybride   
17346            BMW           XM LABEL        2795.0   45   hybride   
20512     LAND ROVER        RANGE ROVER        2800.0  270   essence   
2788      LAND ROVER        RANGE ROVER        2810.0   20   hybride   
2791      LAND ROVER        RANGE ROVER        2810.0   21   hybride   
2592      LAND ROVER  RANGE ROVER SPORT        2810.0   20   hybride   
20189     LAND ROVER        RANGE ROVER        2810.0  269   essence   
2789      LAND ROVER        RANGE ROVER        2810.0   19   hybride   
22567     LAND ROVER        RANGE ROVER        2810.0  268   essence   
16676     LAND ROVER        RANGE ROVER        2810.0   17   hybride   
2593      LAND ROVER  RANGE ROVER SPORT        2810.0   19   hybride   
14674     LAND ROVER        RANGE ROVER        2810.0   18   hybride   
15307     LAND ROVER  RANGE ROVER SPORT        2810.0   17   hybride   
15256     LAND ROVER  RANGE ROVER SPORT        2810.0   17   hybride   
15345     LAND ROVER  RANGE ROVER SPORT        2810.0   18   hybride   
23852          INEOS    INEOS GRENADIER        2815.0  312    diesel   
11578  MERCEDES BENZ      AMG G 63 4X42        2866.0  456   essence   

       Cylindrée moteur  Puissance moteur  Consommation carburant      ICSM  \
23315            4395.0             430.0                     1.8  0.153846   
15627            4395.0             430.0                     1.9  0.153846   
22757            4395.0             430.0                     1.7  0.153846   
17115            4395.0             430.0                     1.8  0.153846   
17346            4395.0             430.0                     2.0  0.153846   
20512            4395.0             452.0                    11.9  0.161429   
2788             2996.0             294.0                     0.9  0.104626   
2791             2996.0             294.0                     0.9  0.104626   
2592             2996.0             294.0                     0.9  0.104626   
20189            4395.0             390.0                    11.9  0.138790   
2789             2996.0             294.0                     0.9  0.104626   
22567            4395.0             390.0                    11.8  0.138790   
16676            2996.0             294.0                     0.8  0.104626   
2593             2996.0             294.0                     0.9  0.104626   
14674            2996.0             294.0                     0.8  0.104626   
15307            2996.0             294.0                     0.8  0.104626   
15256            2996.0             294.0                     0.7  0.104626   
15345            2996.0             294.0                     0.8  0.104626   
23852            2993.0             183.0                    12.2  0.065009   
11578            3982.0             430.0                    20.1  0.150035   

            ICE      IDEC  
23315  0.097838  1.572451  
15627  0.097838  1.572451  
22757  0.097838  1.572451  
17115  0.097838  1.572451  
17346  0.097838  1.572451  
20512  0.102844  1.569643  
2788   0.098131  1.066192  
2791   0.098131  1.066192  
2592   0.098131  1.066192  
20189  0.088737  1.564057  
2789   0.098131  1.066192  
22567  0.088737  1.564057  
16676  0.098131  1.066192  
2593   0.098131  1.066192  
14674  0.098131  1.066192  
15307  0.098131  1.066192  
15256  0.098131  1.066192  
15345  0.098131  1.066192  
23852  0.061143  1.063233  
11578  0.107986  1.389393

## Cylindrée moteur

In [88]:
detecter_outliers_plotly_var(df['Cylindrée moteur'])

Nb_Outliers  Pourcentage
Cylindrée moteur         2616        10.93

In [89]:
df_outliers_CO2 = df[df['Cylindrée moteur'] > 4000].sort_values(by='Cylindrée moteur', ascending=True)
df_outliers_CO2.tail(20)

Marque                      Modèle  Masse à vide  CO2 Carburant  \
18575      FERRARI         FERRARI DAYTONA SP3        1705.0  368   essence   
17392      FERRARI          FERRARI PUROSANGUE        2245.0  393   essence   
14527  LAMBORGHINI                   AVENTADOR        1790.0  442   essence   
14517  LAMBORGHINI                   AVENTADOR        1780.0  440   essence   
14516  LAMBORGHINI        AVENTADOR (COUNTACH)        1780.0  440   essence   
14522  LAMBORGHINI                   AVENTADOR        1740.0  442   essence   
14521  LAMBORGHINI                   AVENTADOR        1715.0  448   essence   
2947   ROLLS-ROYCE                        Dawn        2705.0  368   essence   
22704  ROLLS-ROYCE        CULLINAN BLACK BADGE        2785.0  375   essence   
22118  ROLLS-ROYCE                   GHOST EWB        2605.0  357   essence   
2946   ROLLS-ROYCE        Cullinan Black Badge        2785.0  374   essence   
2943   ROLLS-ROYCE                       Ghost        2565.0  356   essence   
2944   ROLLS-ROYCE                     Phantom        2760.0  354   essence   
2945   ROLLS-ROYCE                     Phantom        2760.0  353   essence   
20025  ROLLS-ROYCE                     PHANTOM        2755.0  360   essence   
18016  ROLLS-ROYCE                    CULLINAN        2765.0  369   essence   
23908  ROLLS-ROYCE                   GHOST EWB        2605.0  350   essence   
5128       BUGATTI    BUGATTI CHIRON PUR SPORT        2070.0  572   essence   
5129       BUGATTI              BUGATTI CHIRON        2070.0  572   essence   
20717      BUGATTI  BUGATTI CHIRON SUPER SPORT        2070.0  487   essence   

       Cylindrée moteur  Puissance moteur  Consommation carburant      ICSM  \
18575            6496.0             614.0                    16.2  0.360117   
17392            6496.0             529.0                    17.3  0.235635   
14527            6498.0             574.0                    18.0  0.320670   
14517            6498.0             574.0                    19.5  0.322472   
14516            6498.0             574.0                    19.5  0.322472   
14522            6498.0             574.0                    18.0  0.329885   
14521            6498.0             566.0                    18.0  0.330029   
2947             6592.0             441.0                    16.2  0.163031   
22704            6749.0             441.0                    16.5  0.158348   
22118            6749.0             420.0                    15.7  0.161228   
2946             6749.0             441.0                    16.4  0.158348   
2943             6749.0             420.0                    15.6  0.163743   
2944             6749.0             420.0                    15.5  0.152174   
2945             6749.0             420.0                    15.5  0.152174   
20025            6749.0             420.0                    15.9  0.152450   
18016            6749.0             420.0                    16.2  0.151899   
23908            6749.0             420.0                    15.4  0.161228   
5128             7993.0            1103.0                    25.2  0.532850   
5129             7993.0            1103.0                    25.2  0.532850   
20717            7993.0            1177.0                    21.5  0.568599   

            ICE      IDEC  
18575  0.094520  3.809971  
17392  0.081435  2.893541  
14527  0.088335  3.630168  
14517  0.088335  3.650562  
14516  0.088335  3.650562  
14522  0.088335  3.734483  
14521  0.087104  3.788921  
2947   0.066899  2.436969  
22704  0.065343  2.423339  
22118  0.062231  2.590787  
2946   0.065343  2.423339  
2943   0.062231  2.631189  
2944   0.062231  2.445290  
2945   0.062231  2.445290  
20025  0.062231  2.449728  
18016  0.062231  2.440868  
23908  0.062231  2.590787  
5128   0.137996  3.861353  
5129   0.137996  3.861353  
20717  0.147254  3.861353

## CO2

In [90]:
detecter_outliers_plotly_var(df['CO2'])

Nb_Outliers  Pourcentage
CO2         3895        16.27

In [91]:
df_outliers_CO2 = df[df['CO2'] > 400].sort_values(by='CO2', ascending=True)
df_outliers_CO2.tail(20)

Marque                      Modèle  Masse à vide  CO2 Carburant  \
14516    LAMBORGHINI        AVENTADOR (COUNTACH)        1780.0  440   essence   
14517    LAMBORGHINI                   AVENTADOR        1780.0  440   essence   
14522    LAMBORGHINI                   AVENTADOR        1740.0  442   essence   
14527    LAMBORGHINI                   AVENTADOR        1790.0  442   essence   
14521    LAMBORGHINI                   AVENTADOR        1715.0  448   essence   
11578  MERCEDES BENZ               AMG G 63 4X42        2866.0  456   essence   
19997  MERCEDES BENZ               AMG G 63 4X42        2595.0  456   essence   
20717        BUGATTI  BUGATTI CHIRON SUPER SPORT        2070.0  487   essence   
5129         BUGATTI              BUGATTI CHIRON        2070.0  572   essence   
5128         BUGATTI    BUGATTI CHIRON PUR SPORT        2070.0  572   essence   

       Cylindrée moteur  Puissance moteur  Consommation carburant      ICSM  \
14516            6498.0             574.0                    19.5  0.322472   
14517            6498.0             574.0                    19.5  0.322472   
14522            6498.0             574.0                    18.0  0.329885   
14527            6498.0             574.0                    18.0  0.320670   
14521            6498.0             566.0                    18.0  0.330029   
11578            3982.0             430.0                    20.1  0.150035   
19997            3982.0             430.0                    20.1  0.165703   
20717            7993.0            1177.0                    21.5  0.568599   
5129             7993.0            1103.0                    25.2  0.532850   
5128             7993.0            1103.0                    25.2  0.532850   

            ICE      IDEC  
14516  0.088335  3.650562  
14517  0.088335  3.650562  
14522  0.088335  3.734483  
14527  0.088335  3.630168  
14521  0.087104  3.788921  
11578  0.107986  1.389393  
19997  0.107986  1.534489  
20717  0.147254  3.861353  
5129   0.137996  3.861353  
5128   0.137996  3.861353

## Puissance moteur

In [92]:
detecter_outliers_plotly_var(df['Puissance moteur'])

Nb_Outliers  Pourcentage
Puissance moteur         2575        10.76

In [93]:
df_outliers_Consommation = df[df['Puissance moteur'] > 15].sort_values(by='Puissance moteur', ascending=True)
df_outliers_Consommation.tail(20)

Marque                      Modèle  Masse à vide  CO2 Carburant  \
19122  ASTON MARTIN    DBS 770 ULTIMATE VOLANTE        2020.0  314   essence   
14521   LAMBORGHINI                   AVENTADOR        1715.0  448   essence   
17722  ASTON MARTIN            DBS 770 ULTIMATE        2020.0  314   essence   
14509       FERRARI               SF90 STRADALE        1850.0  154   hybride   
14516   LAMBORGHINI        AVENTADOR (COUNTACH)        1780.0  440   essence   
14511       FERRARI                 SF90 SPIDER        1905.0  162   hybride   
14527   LAMBORGHINI                   AVENTADOR        1790.0  442   essence   
14522   LAMBORGHINI                   AVENTADOR        1740.0  442   essence   
14508       FERRARI               SF90 STRADALE        1820.0  160   hybride   
14510       FERRARI                 SF90 SPIDER        1925.0  149   hybride   
14517   LAMBORGHINI                   AVENTADOR        1780.0  440   essence   
14512       FERRARI                     812 GTS        1865.0  373   essence   
14507       FERRARI                   MONZA SP2        1706.0  366   essence   
14506       FERRARI                   MONZA SP1        1685.0  366   essence   
19565       FERRARI          812 COMPETIZIONE A        1810.0  370   essence   
14501       FERRARI            812 COMPETIZIONE        1740.0  385   essence   
18575       FERRARI         FERRARI DAYTONA SP3        1705.0  368   essence   
5128        BUGATTI    BUGATTI CHIRON PUR SPORT        2070.0  572   essence   
5129        BUGATTI              BUGATTI CHIRON        2070.0  572   essence   
20717       BUGATTI  BUGATTI CHIRON SUPER SPORT        2070.0  487   essence   

       Cylindrée moteur  Puissance moteur  Consommation carburant      ICSM  \
19122            5204.0             566.0                    13.9  0.280198   
14521            6498.0             566.0                    18.0  0.330029   
17722            5204.0             566.0                    13.9  0.280198   
14509            3990.0             574.0                     6.1  0.310270   
14516            6498.0             574.0                    19.5  0.322472   
14511            3990.0             574.0                     6.4  0.301312   
14527            6498.0             574.0                    18.0  0.320670   
14522            6498.0             574.0                    18.0  0.329885   
14508            3990.0             574.0                     6.0  0.315385   
14510            3990.0             574.0                     6.1  0.298182   
14517            6498.0             574.0                    19.5  0.322472   
14512            6496.0             585.0                    16.4  0.313673   
14507            6496.0             592.0                    16.1  0.347011   
14506            6496.0             592.0                    16.1  0.351335   
19565            6496.0             607.0                    16.3  0.335359   
14501            6496.0             607.0                    16.9  0.348851   
18575            6496.0             614.0                    16.2  0.360117   
5128             7993.0            1103.0                    25.2  0.532850   
5129             7993.0            1103.0                    25.2  0.532850   
20717            7993.0            1177.0                    21.5  0.568599   

            ICE      IDEC  
19122  0.108762  2.576238  
14521  0.087104  3.788921  
17722  0.108762  2.576238  
14509  0.143860  2.156757  
14516  0.088335  3.650562  
14511  0.143860  2.094488  
14527  0.088335  3.630168  
14522  0.088335  3.734483  
14508  0.143860  2.192308  
14510  0.143860  2.072727  
14517  0.088335  3.650562  
14512  0.090055  3.483110  
14507  0.091133  3.807737  
14506  0.091133  3.855193  
19565  0.093442  3.588950  
14501  0.093442  3.733333  
18575  0.094520  3.809971  
5128   0.137996  3.861353  
5129   0.137996  3.861353  
20717  0.147254  3.861353

## Consommation carburant

In [95]:
detecter_outliers_plotly_var(df['Consommation carburant'])

Nb_Outliers  Pourcentage
Consommation carburant         3410        14.25

In [ ]:
df_outliers_Consommation = df[df['Consommation carburant'] > 15].sort_values(by='Consommation carburant', ascending=True)
df_outliers_Consommation.tail(20)

# <font color='#3585CD'>Visualisation globale graphique</font>

In [96]:
fig = px.scatter_matrix(df, dimensions=df.select_dtypes(include=['number']).columns,
                        color='Carburant', title="Pairplot")

fig.update_layout(height=900, width=1200)
fig.show()

In [97]:
plot_correlation_matrix(df)

# <font color='#3585CD'>Distribution de la variable cible</font>





## Histogramme et boxplot de la variable cible

In [98]:
analyser_variables_numeriques_plotly(df, ['CO2'])

In [99]:
import plotly.graph_objects as go
import numpy as np
import scipy.stats as stats
import pandas as pd

# Calcul des quantiles
(quantiles, values), (slope, intercept, r) = stats.probplot(df['CO2'], dist="norm")

# Création du Q-Q Plot avec Plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=quantiles, y=values, mode='markers', name='Données'))
fig.add_trace(go.Scatter(x=quantiles, y=slope * np.array(quantiles) + intercept, mode='lines', name='Ligne théorique'))

fig.update_layout(title='Q-Q plot pour CO2', xaxis_title='Quantiles théoriques', yaxis_title='Quantiles des données')

fig.show()

In [100]:
from statsmodels.stats.diagnostic import lilliefors
# Niveau de signification (alpha)
alpha = 0.05

# Effectuer les tests de normalité
shapiro_test = stats.shapiro(df['CO2'])
ks_test = stats.kstest(df['CO2'], 'norm')
ad_test = stats.anderson(df['CO2'], dist='norm')
dagostino_test = stats.normaltest(df['CO2'])
lilliefors_test = lilliefors(df['CO2'], dist='norm')

# Créer un tableau pandas avec les résultats des tests
test_results = pd.DataFrame({
    'Nom du test': ['Shapiro-Wilk', 'Kolmogorov-Smirnov', 'Anderson-Darling', "D'Agostino-Pearson", 'Lilliefors'],
    'Statistique de test': [shapiro_test[0], ks_test.statistic, ad_test.statistic, dagostino_test.statistic, lilliefors_test[0]],
    'p-valeur': [shapiro_test[1], ks_test.pvalue, None, dagostino_test.pvalue, lilliefors_test[1]],
    'Normalité': ['Oui' if shapiro_test[1] > alpha else 'Non',
                  'Oui' if ks_test.pvalue > alpha else 'Non',
                  'Oui' if any(ad_test.statistic < crit_val for crit_val in ad_test.critical_values) else 'Non',
                  'Oui' if dagostino_test.pvalue > alpha else 'Non',
                  'Oui' if lilliefors_test[1] > alpha else 'Non']
})

print(test_results)


          Nom du test  Statistique de test      p-valeur Normalité
0        Shapiro-Wilk             0.895421  1.114616e-81       Non
1  Kolmogorov-Smirnov             1.000000  0.000000e+00       Non
2    Anderson-Darling           960.532022           NaN       Non
3  D'Agostino-Pearson          1891.924362  0.000000e+00       Non
4          Lilliefors             0.171282  1.000000e-03       Non


In [ ]:
# from scipy.stats import boxcox

# df['co2_transformed'], lambda_boxcox = boxcox(df['Ewltp (g/km)'] + 1)  # Ajouter 1 pour éviter 0
# df

In [101]:
df['Carburant'].unique()

array(['hybride', 'essence', 'diesel', 'gaz', 'e85'], dtype=object)

In [102]:
# Histogramme en fonction du type de motorisation
fig = px.histogram(df, x="CO2", color="Carburant", nbins=50, barmode="overlay",
                   title="Distribution des émissions de CO2 par type de carburant")
fig.show()


Comment gérer ?


*   Création colonne Hybride ?
*   Dataset à part ?
*   Juste un OneHotEncoder ?

## Degrés d'asymétrie des variables

In [103]:
num_vars = df.select_dtypes(include=['int64', 'float64']).columns.tolist()
df[num_vars].skew().sort_values()

CO2                       0.100928
Consommation carburant    0.385213
ICE                       0.796035
Masse à vide              0.822773
Cylindrée moteur          1.878756
IDEC                      2.209121
Puissance moteur          2.748144
ICSM                      3.261179
dtype: float64

### CO2

Légère asymétrie négative (peu inquiétante)

### Consommation carburant

 Quasi symétrique (très léger)

### Masse moyenne

Asymétrie positive modérée à forte, probablement due à des valeurs élevées qui tirent la distribution.

# <font color='#3585CD'>Quelles variables garder pour prédire le CO2 ?</font>

Selon nous, les **variables pertinentes** à garder pour la prédiction sont les suivantes :
* **Masse à vide** : un véhicule plus lourd a souvent des émissions plus élevées.
* **Cylindrée moteur** : une plus grande cylindrée est souvent associée à une plus grande consommation et donc plus d’émissions.
* **Puissance moteur** : un moteur plus puissant a tendance à consommer plus de carburant.
* **Carburant** : Essence, diesel, hybride… Chaque type influence les émissions. La variable Carburant sera encodée.

* **Consommation carburant** : directement liée aux émissions de CO2. Cependant sa forte corrélation peut expliquer à elle seule les émissions de CO2. Nous nous questionnerons au moment de la modélisation si nous la gardons ou pas.

Nous **excluerons** les variables **Marque** et **Modèle** qui ne sont pas directement liées aux émissions de CO2.

Pourquoi exclure les variables **Marque** et **Modèle** ?
* Ce sont des variables catégoriques à très haute **cardinalité**
* L'influence sur le CO₂ passe par des **caractéristiques techniques**

# <font color='#3585CD'>Export du dataset nettoyé</font>

In [104]:
df.shape

(23935, 11)

In [105]:
df = df.reset_index(drop=True)
df

Marque              Modèle  Masse à vide  CO2 Carburant  \
0               JEEP            RENEGADE        1845.0   49   hybride   
1               JEEP            WRANGLER        1883.0  244   essence   
2               JEEP            WRANGLER        1972.0  259   essence   
3               JEEP            WRANGLER        1972.0  258   essence   
4               JEEP  WRANGLER UNLIMITED        2348.0   79   hybride   
...              ...                 ...           ...  ...       ...   
23930          SKODA               SCALA        1211.0  119   essence   
23931           FORD      TRANSIT CUSTOM        2311.0  197    diesel   
23932  MERCEDES BENZ               A 200        1440.0  144   essence   
23933  MERCEDES BENZ            V-KLASSE        2220.0  225    diesel   
23934           FORD      TRANSIT CUSTOM        2167.0  205    diesel   

       Cylindrée moteur  Puissance moteur  Consommation carburant      ICSM  \
0                1332.0              96.0                     2.0  0.052033   
1                1995.0             200.0                    10.8  0.106213   
2                1995.0             200.0                    11.5  0.101420   
3                1995.0             200.0                    11.5  0.101420   
4                1995.0             200.0                     3.5  0.085179   
...                 ...               ...                     ...       ...   
23930             999.0              70.0                     5.2  0.057803   
23931            1995.0              95.0                     7.5  0.041108   
23932            1332.0             120.0                     6.3  0.083333   
23933            1950.0             174.0                     8.6  0.078378   
23934            1995.0              95.0                     7.8  0.043839   

            ICE      IDEC  
0      0.072072  0.721951  
1      0.100251  1.059480  
2      0.100251  1.011663  
3      0.100251  1.011663  
4      0.100251  0.849659  
...         ...       ...  
23930  0.070070  0.824938  
23931  0.047619  0.863263  
23932  0.090090  0.925000  
23933  0.089231  0.878378  
23934  0.047619  0.920628  

[23935 rows x 11 columns]

In [106]:
# Vérifier si on est sur Google Colab
import os
try:
    import google.colab
    ON_COLAB = True
    dataset_path = "/content/drive/My Drive/Formation DS/Projet CO2/NOV24-CDS-CO2/notebooks/datasets/Dataset_final/datas_nettoyees_model_FR.csv"

    # Monter Google Drive si ce n'est pas déjà fait
    from google.colab import drive
    drive.mount('/content/drive')

except ImportError:
    ON_COLAB = False
    dataset_path = "datasets/Dataset_final/datas_nettoyees_model_FR.csv"

# Sauvegarde du DataFrame
df.to_csv(dataset_path, index=False)

# Vérification de l'enregistrement
if os.path.exists(dataset_path):
    print(f"Le fichier a bien été enregistré à l'emplacement : {dataset_path}")
else:
    print("Problème lors de l'enregistrement du fichier.")


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Le fichier a bien été enregistré à l'emplacement : /content/drive/My Drive/Formation DS/Projet CO2/NOV24-CDS-CO2/notebooks/datasets/Dataset_final/datas_nettoyees_model_FR.csv


In [ ]:
# dataset_path = "datasets/Dataset_final/datas_nettoyees_model_FR.csv"
# df.to_csv(dataset_path, index =False)

# import os

# # Vérifie si le fichier existe
# if os.path.exists(dataset_path):
#     print("Le fichier a bien été enregistré.")
# else:
#     print("Problème lors de l'enregistrement du fichier.")
